### Create the process for merging new or corrected site data

In [101]:
import geopandas as gpd
import pandas as pd
import numpy as np
import os
import folium
# use these if you are using the pandas dataframe view, I prefer itables because it is interactive
# pd.set_option('display.max_columns', None)
# pd.set_option('display.max_rows', None)

# this makes dataframes viewable as interactive tables with search and sort
from itables import init_notebook_mode
init_notebook_mode(all_interactive=True)

import itables.options as opt
opt.maxBytes = 0 ### this removes size limits for interactive table


<IPython.core.display.Javascript object>

#### ** helpful links and snippets

In [102]:
# os.getcwd() # check what the working directory is

# keyboard shortcuts
# https://noteable.io/blog/jupyter-notebook-shortcuts-boost-productivity/

### set working directory to the github repo directory
this is where you change this so that it works on your computer too

In [103]:
os.chdir('/Users/sarahodges/spatial/SAVI/hudson_access/data/published')

### Import existing site points data

 - this is actually the **hap_site_points_fieldupdates_surveyintegration_8-2-23.geojson** data from sara eichner, with the new entries removed from the dataset
 - using this to create the process of site data updates

In [104]:
current_site_points = gpd.read_file('data/hap_site_points.geojson')
# len(current_site_points.columns)
current_site_points

site_id         act_codes                             access_id  \
0            174  FISH, HPBL, MPBL                      4, 516, 151, 787   
1             29  MPBL, HPBL, FISH                   126, 83, 1613, 1803   
2            183              FISH                      1, 443, 511, 800   
3             54  MPBL, HPBL, FISH     291, 433, 293, 166, 117, 000, 000   
4              1              HPBL  9, 097, 941, 594, 168, 710, 000, 000   
..           ...               ...                                   ...   
747  remove dupe              MPBL                                   509   
748          215              HPBL                     16, 752, 031, 621   
749        71975              HPBL                             1621_HPBL   
750          157  MPBL, HPBL, FISH                           3, 121, 599   
751          161              FISH                      1, 517, 201, 721   

                                site_name                   site_label  \
0                          Bayswater Park                         None   
1                   Conference House Park                         None   
2                 Mt Loretto Natural Area                         None   
3                        Lemon Creek Park                         None   
4                          Riverside Park                         None   
..                                    ...                          ...   
747                      River Barge Park                         None   
748             Gowanus Canal Sponge Park                         None   
749  Lowe's Gowanus Parklet & Boat Launch                         None   
750               Louis Valentino Jr Park                         None   
751                       Shore Road Park  Shore Road Park and Parkway   

                                          site_address  \
0    Dwight Ave, Seagirt Blvd between Beach 38th St...   
1    Hylan Blvd & Satterlee St, Staten Island, Hyla...   
2    End of Sharrotts Ave at Hylan Blvd, Hylan Blvd...   
3                                                 None   
4                             W 79th St End, Manhattan   
..                                                 ...   
747                                               None   
748               166 2nd St, Brooklyn, Foot of 2nd St   
749                   539 Smith St, Brooklyn, NY 11231   
750               End of Coffey St, Red Hook, Brooklyn   
751     Bay Ridge Ave (69th St) at Shore Rd, Bay Ridge   

                                      site_description  \
0    This waterfront park is named, in part, for Ju...   
1    The site of a legendary display of American de...   
2                                                 None   
3                             Yellow trail nature path   
4    This site is considered a cultural resource. R...   
..                                                 ...   
747                                               None   
748                                               None   
749                                               None   
750  Now surrounded by industrial, residential, and...   
751  An expansive park along the Shore Parkway Gree...   

                                    hours_info open_close_date   fee  ...  \
0    Sunrise to Sunset (April 1 to December 1)            None  None  ...   
1    Sunrise to Sunset (April 1 to December 1)            None     Y  ...   
2                                         None            None  None  ...   
3                                         None            None  None  ...   
4    Sunrise to Sunset (April 1 to December 1)            None  None  ...   
..                                         ...             ...   ...  ...   
747                                       None            None  None  ...   
748                                       None            None  None  ...   
749                                       None            None  None  ...   
750  Sunrise to Sunset (April 1 to December

In [105]:
#### create a site_score dataframe and remove from data
site_score = current_site_points.copy()[['site_id', 'site_score']]
#site_score.head()
# site_points.columns.to_list()

### Make corrections to existing site points data

In [106]:
# Filtering and Mutating operations
site_points = (
    current_site_points
    .query("site_id != 'remove dupe'")
    .drop(columns='site_score')  # Remove the 'site_score' column
    .assign(
        site_name=current_site_points["site_name"].where(current_site_points["site_name"] != "Fair Haven Rd & Fairwaters Lane", "Fair Haven Pier"),
        site_id=current_site_points["site_id"].where(current_site_points["site_name"] != "Fair Haven Rd & Fairwaters Lane", 540232),
        site_description=current_site_points['site_description'].str.replace('This site is considered an historic landmark', ''),
        url_public = current_site_points['url_public'].str.split(",").str[0]  ### keep only the first url if there is nore than one 
    )
)

# remove the extra Bayswater Point State Park
site_points = site_points[site_points["site_id"] != "159127"]
site_points.loc[site_points['site_id'] == '154', 'url_public'] = "https://www.nycgovparks.org/parks/leon-s-kaiser-park"

# site_points['site_id'] = pd.to_numeric(site_points['site_id'], errors='coerce')  
### the highest site_id (other than one that ends in 999 for a specific reason, is 900136)

site_points_df = pd.DataFrame(site_points.drop(columns='geometry'))
site_points_df

site_id         act_codes                             access_id  \
0       174  FISH, HPBL, MPBL                      4, 516, 151, 787   
1        29  MPBL, HPBL, FISH                   126, 83, 1613, 1803   
2       183              FISH                      1, 443, 511, 800   
3        54  MPBL, HPBL, FISH     291, 433, 293, 166, 117, 000, 000   
4         1              HPBL  9, 097, 941, 594, 168, 710, 000, 000   
..      ...               ...                                   ...   
746      98  MPBL, FISH, HPBL                      6, 416, 501, 784   
748     215              HPBL                     16, 752, 031, 621   
749   71975              HPBL                             1621_HPBL   
750     157  MPBL, HPBL, FISH                           3, 121, 599   
751     161              FISH                      1, 517, 201, 721   

                                site_name                   site_label  \
0                          Bayswater Park                         None   
1                   Conference House Park                         None   
2                 Mt Loretto Natural Area                         None   
3                        Lemon Creek Park                         None   
4                          Riverside Park                         None   
..                                    ...                          ...   
746       Breezy Point Tip at Jamaica Bay                         None   
748             Gowanus Canal Sponge Park                         None   
749  Lowe's Gowanus Parklet & Boat Launch                         None   
750               Louis Valentino Jr Park                         None   
751                       Shore Road Park  Shore Road Park and Parkway   

                                          site_address  \
0    Dwight Ave, Seagirt Blvd between Beach 38th St...   
1    Hylan Blvd & Satterlee St, Staten Island, Hyla...   
2    End of Sharrotts Ave at Hylan Blvd, Hylan Blvd...   
3                                                 None   
4                             W 79th St End, Manhattan   
..                                                 ...   
746  End of Rockaway Point Blvd, Beach 222nd Street...   
748               166 2nd St, Brooklyn, Foot of 2nd St   
749                   539 Smith St, Brooklyn, NY 11231   
750               End of Coffey St, Red Hook, Brooklyn   
751     Bay Ridge Ave (69th St) at Shore Rd, Bay Ridge   

                                      site_description  \
0    This waterfront park is named, in part, for Ju...   
1    The site of a legendary display of American de...   
2                                                 None   
3                             Yellow trail nature path   
4    This site is considered a cultural resource. R...   
..                                                 ...   
746  It’s easy to forget one is in New York City at...   
748                                               None   
749                                               None   
750  Now surrounded by industrial, residential, and...   
751  An expansive park along the Shore Parkway Gree...   

                                    hours_info open_close_date   fee  ...  \
0    Sunrise to Sunset (April 1 to December 1)            None  None  ...   
1    Sunrise to Sunset (April 1 to December 1)            None     Y  ...   
2                                         None            None  None  ...   
3                                         None            None  None  ...   
4    Sunrise to Sunset (April 1 to December 1)            None  None  ...   
..                                         ...             ...   ...  ...   
746                                       None            None  None  ...   
748                                       None            None  None  ...   
749                                       None            None  None  ...   
750  Sunrise to Sunset (April 1 to December 1)            None  None  ...   
751                  

## IMPORT survey data from summer site visits and process
Alyssa collected these over the summer - up to July 28 using the Survey123 s

In [125]:
## add new survey data
raw_surv_new = pd.read_csv('data/data_updates/Hudson_Access_Project_Data_Survey_0.csv')

#### Function to create new act_codes based on Alyssa's YN columns

 - if none are defined as Y, then act_codes == VISUAL
 - discuss with Sara E, we decided to define them all as FISH, but when I looked at them it didn;t seem right

In [109]:
def create_new_act_codes(row):
    activities = []
    if row['FISH_YN'] == 'Y':
        activities.append('FISH')
    if row['SWIM_YN'] == 'Y':
        activities.append('SWIM')
    if row['HPBL_YN'] == 'Y':
        activities.append('HPBL')
    if row['MPBL_YN'] == 'Y':
        activities.append('MPBL')
        
    if not activities:
        activities.append('VISUAL')
    
    return ','.join(activities)

#### Handle new sites

 - create dataframe of sites that aren't in the existing dataset
 - add source info
 - add site_id
 - check and update act_codes

In [110]:
# add site_id to all the new sites

new_sites = (
    raw_surv_new
    .query("site_id == 'needs id'")
    .assign(
        source = "Alyssa, summer 23 new site"
    )
    .reset_index(drop=True)
)

new_sites['site_id'] = new_sites.index + 900137 ### the highest site_id (other than one that ends in 999 for a specific reason, is 900136)

In [111]:
new_sites['act_codes'] = new_sites.apply(create_new_act_codes, axis=1)

new_sites

ObjectID                              GlobalID county  lat  lon  \
0         45  45838631-7518-41eb-88ed-83f029354329    NaN  NaN  NaN   
1         58  ce0c11d9-c208-47be-8ea0-6c85319c077a    NaN  NaN  NaN   
2         57  6101c1a0-d8f7-4854-8034-9bb337ec231e    NaN  NaN  NaN   
3         46  df04d5fe-95b2-44ad-8d6c-1a3dd770f31f    NaN  NaN  NaN   
4         41  6095d94b-8a52-4368-8a99-1f2088a690f0    NaN  NaN  NaN   
5         56  7fd1fede-5f52-4c57-85bb-206accf6490c    NaN  NaN  NaN   
6         36  26b60cc7-0f57-49f6-8efa-e16ec0ddf0a2    NaN  NaN  NaN   
7         47  5e0fd162-5841-4784-8510-7786ef285ce4    NaN  NaN  NaN   
8         35  2ef63fac-3550-43fd-8041-d1f77a2b375e    NaN  NaN  NaN   
9         38  b9a61410-d38b-4e79-88ee-cfc5f723fb58    NaN  NaN  NaN   
10        44  4fe69fc5-ce1e-4e3d-86f2-c08ee115b7d3    NaN  NaN  NaN   
11        59  34e95d22-a291-4777-86bf-2081c92aa57a    NaN  NaN  NaN   
12        53  50241fa8-f460-42e5-8cf4-3551107853d1    NaN  NaN  NaN   

   municipality natural_no  site_id access_id                      source  \
0           NaN        NaN   900137       NaN  Alyssa, summer 23 new site   
1           NaN        NaN   900138       NaN  Alyssa, summer 23 new site   
2           NaN        NaN   900139       NaN  Alyssa, summer 23 new site   
3           NaN        NaN   900140       NaN  Alyssa, summer 23 new site   
4           NaN        NaN   900141       NaN  Alyssa, summer 23 new site   
5           NaN        NaN   900142       NaN  Alyssa, summer 23 new site   
6           NaN        NaN   900143       NaN  Alyssa, summer 23 new site   
7           NaN        NaN   900144       NaN  Alyssa, summer 23 new site   
8           NaN        NaN   900145       NaN  Alyssa, summer 23 new site   
9           NaN        NaN   900146       NaN  Alyssa, summer 23 new site   
10          NaN        NaN   900147       NaN  Alyssa, summer 23 new site   
11          NaN        NaN   900148       NaN  Alyssa, summer 23 new site   
12          NaN        NaN   900149       NaN  Alyssa, summer 23 new site   

    ... access_type access_type_other water_depth_est  \
0   ...        pier               NaN             NaN   
1   ...        pier               NaN             NaN   
2   ...       rocky               NaN             NaN   
3   ...       rocky               NaN             NaN   
4   ...       beach               NaN             NaN   
5   ...        dock               NaN             NaN   
6   ...       rocky               NaN             NaN   
7   ...        pier               NaN             NaN   
8   ...         NaN               NaN             NaN   
9   ...         NaN               NaN             NaN   
10  ...         NaN               NaN             NaN   
11  ...  pier,rocky               NaN             NaN   
12  ...       other     Floating Lab              NaN   

                             water_quality_monitoring  \
0                                                 NaN   
1                                                 NaN   
2                                                 NaN   
3   https://www.riverkeeper.org/water-quality/huds...   
4   https://www.riverkeeper.org/water-quality/citi...   
5                                                 NaN   
6   https://www.riverkeeper.org/water-quality/citi...   
7   https://www.riverkeeper.org/water-quality/huds...   
8   https://www.riverkeeper.org/water-quality/huds...   
9   https://www.weatherlink.com/embeddablePage/sho...   
10                                                NaN   
11  https://www.riverkeeper.org/water-quality/huds...   
12  https://www.riverkeeper.org/water-quality/huds...   

                                     open_close_date walking_trails  \
0                                                NaN            NaN   
1                                                NaN              Y   
2                                                NaN              Y   
3                                               

#### Handle updated sites

 - create dataframe of sites that are in the existing dataset
 - add spource info
 - create dataframe of information in old hap_site_points to check if there are any issues
 - check and update act_codes

In [112]:
## create a dataframe of updated site_ids 

updated_sites = (
    raw_surv_new
    .query("site_id != 'needs id'")
    .assign(
        source = "Alyssa, summer 23 updated site",
        act_codes = raw_surv_new.apply(create_new_act_codes, axis=1)
    )
    # .filter(['site_id', 'site_name'], axis="columns") # first look at the names to check
)

#updated_sites

# this is the old sites, can use this to compare later
replaced_sites = site_points_df.merge(updated_sites[['site_id']], on='site_id', how='inner')

# explored in the console
# len(updated_sites) = 18
# len(replaced_sites) = 19
### there is a dupe in the original data, I will make sure it is removed when I bind all the dfs togther

### Create a global id - site id key for new sites to add activity points

In [272]:
### create global id - site id key to join activity point locations added in survey to the current activity points
updated_temp = updated_sites[['GlobalID', 'site_id', 'site_name']].copy()
new_temp = new_sites[['GlobalID', 'site_id', 'site_name']].copy()
global_key = pd.concat([updated_temp, new_temp], ignore_index=True)
global_key

GlobalID site_id  \
0   da1362e6-2cd3-4d8e-8248-83e909a7604e     194   
1   601f9e86-b4f3-4b5a-860d-fa255b8a2252     146   
2   47c4241e-a062-4f7e-89a8-e61c907f61b3       3   
3   1529e54f-04f9-4e20-8206-3a67ea8e3f98      45   
4   db51d0bf-d276-43e0-8df7-3609ad6f04e5     184   
5   46b27436-f308-445b-8144-40e95a64bcd0     134   
6   17ea1535-9129-40d0-822f-6d49628a4bed     231   
7   37c92bd7-6418-4092-873f-77a9367a51aa     192   
8   8a64f7d3-ba3a-4859-817d-fcc2132983f0  900124   
9   69afba0a-23df-4a17-8f32-9cca3e99d264  900133   
10  a0ac502e-6ea8-4c64-8ef5-c0e1ff10665e     157   
11  2446f541-de5b-4b1b-84d0-973d1f66cf4b   71975   
12  dec09f6d-34e1-4a30-8582-355f85e7e7e9   79502   
13  29390baf-6222-415a-8ec2-2a8b8024c3d9  649119   
14  acca971b-396f-448a-8e8f-e0b66097472e     161   
15  20e3b9b4-b2e7-4c3d-8e79-ea9892f1f7fc  595580   
16  00f52bae-03be-4081-8f06-cc30ca5c51b9      94   
17  e5af35fa-5127-4d20-8628-134526d1c6c3  645755   
18  45838631-7518-41eb-88ed-83f029354329  900137   
19  ce0c11d9-c208-47be-8ea0-6c85319c077a  900138   
20  6101c1a0-d8f7-4854-8034-9bb337ec231e  900139   
21  df04d5fe-95b2-44ad-8d6c-1a3dd770f31f  900140   
22  6095d94b-8a52-4368-8a99-1f2088a690f0  900141   
23  7fd1fede-5f52-4c57-85bb-206accf6490c  900142   
24  26b60cc7-0f57-49f6-8efa-e16ec0ddf0a2  900143   
25  5e0fd162-5841-4784-8510-7786ef285ce4  900144   
26  2ef63fac-3550-43fd-8041-d1f77a2b375e  900145   
27  b9a61410-d38b-4e79-88ee-cfc5f723fb58  900146   
28  4fe69fc5-ce1e-4e3d-86f2-c08ee115b7d3  900147   
29  34e95d22-a291-4777-86bf-2081c92aa57a  900148   
30  50241fa8-f460-42e5-8cf4-3551107853d1  900149   

                                      site_name  
0                          Bay Ridge Kite Field  
1                           Bushwick Inlet Park  
2                             Calvert Vaux Park  
3                  Canarsie Pier at Jamaica Bay  
4                     Columbia Street Esplanade  
5                         East River State Park  
6                               Erie Basin Park  
7                          Hallett's Cove Beach  
8                    Hudson River Park, Pier 26  
9                    Hudson River Park, Pier 84  
10                      Louis Valentino Jr Park  
11         Lowe's Gowanus Parklet & Boat Launch  
12                     North 5th St Pier & Park  
13                  Shirley Chisholm State Park  
14                              Shore Road Park  
15                  Steuben House Historic Site  
16                        WNYC Transmitter Park  
17                           Yonkers Yacht Club  
18              American Veterans Memorial Pier  
19                             Bensonhurst Park  
20                   Brooklyn Bay Center at BJs  
21                     Bush Terminal Piers Park  
22                                Canarsie Park  
23                     Empire City Water Sports  
24        Fairway Promenade at Red Hook Stores   
25                       Greenpoint Public Park  
26                            Lowlands Nursery   
27                                MARY A WHALEN  
28                    Narrows Botanical Gardens  
29                   Pier 44 Waterfront Garden   
30  RETI Field Station at Gowanus Bay Terminal

## Create updated hap_site_points

 - use antijoin to remove the sites that have been updated
 - concat to combine old, updated, and new

In [113]:
# antijoin
sites_no_update = site_points_df.merge(updated_sites[['site_id']], how='left', indicator=True).query('_merge == "left_only"').drop('_merge', axis="columns")

### test to determine if the antijoin worked as predicted, should == 0
len(site_points_df) - len(replaced_sites) - len(sites_no_update)

0

In [114]:
new_hap_site_points_temp = pd.concat([sites_no_update, updated_sites], ignore_index=True)

#### checks

len(new_hap_site_points_temp)
# 750, good, it removed the dupe in the og data

749

In [133]:
new_hap_site_points = pd.concat([new_hap_site_points_temp, new_sites], ignore_index=True)
len(new_hap_site_points)
# 763 = correct

762

### Checks to ensure that the new data will work with the website

 - act_codes have no spaces
 - all sites have act_codes
 - all sites have site_id

In [116]:
### remove spaces in the act_codes

new_hap_site_points['act_codes'] = new_hap_site_points['act_codes'].str.replace(r'\s*,\s*', ',')


In [117]:
### check for spaces or NAs - will need to figure out what to do about VISUAL and STE

new_hap_site_points['act_codes'].unique()

array(['FISH,HPBL,MPBL', 'MPBL,HPBL,FISH', 'FISH', 'HPBL',
       'FISH,MPBL,HPBL', 'HPBL,MPBL', 'MPBL', 'SWIM', 'HPBL,FISH',
       'MPBL,FISH', 'MPBL,HPBL', 'FISH,SWIM', 'FISH,HPBL', 'HPBL,STE',
       'MPBL,FISH,SWIM,HPBL', 'HPBL,MPBL,FISH', 'MPBL,HPBL,FISH,SWIM',
       'FISH,MPBL', 'SWIM,FISH', 'HPBL,SWIM,MPBL', 'MPBL,SWIM',
       'HPBL,FISH,MPBL', 'MPBL,HPBL,SWIM,FISH', 'MPBL,SWIM,HPBL,FISH',
       'SWIM,MPBL,HPBL,FISH', 'HPBL,SWIM,FISH', 'SWIM,FISH,HPBL',
       'HPBL,SWIM', 'MPBL,FISH,HPBL', 'FISH,SWIM,MPBL,HPBL',
       'FISH,MPBL,HPBL,SWIM', 'MPBL,FISH,SWIM', 'VISUAL'], dtype=object)

In [118]:
### count the NA site_ids

new_hap_site_points['site_id'].isna().sum() 

0

In [119]:
new_hap_site_points

site_id       act_codes                             access_id  \
0       174  FISH,HPBL,MPBL                      4, 516, 151, 787   
1        29  MPBL,HPBL,FISH                   126, 83, 1613, 1803   
2       183            FISH                      1, 443, 511, 800   
3        54  MPBL,HPBL,FISH     291, 433, 293, 166, 117, 000, 000   
4         1            HPBL  9, 097, 941, 594, 168, 710, 000, 000   
..      ...             ...                                   ...   
757  900145          VISUAL                                   NaN   
758  900146          VISUAL                                   NaN   
759  900147          VISUAL                                   NaN   
760  900148            FISH                                   NaN   
761  900149          VISUAL                                   NaN   

                                       site_name site_label  \
0                                 Bayswater Park       None   
1                          Conference House Park       None   
2                        Mt Loretto Natural Area       None   
3                               Lemon Creek Park       None   
4                                 Riverside Park       None   
..                                           ...        ...   
757                            Lowlands Nursery         NaN   
758                                MARY A WHALEN        NaN   
759                    Narrows Botanical Gardens        NaN   
760                   Pier 44 Waterfront Garden         NaN   
761  RETI Field Station at Gowanus Bay Terminal         NaN   

                                          site_address  \
0    Dwight Ave, Seagirt Blvd between Beach 38th St...   
1    Hylan Blvd & Satterlee St, Staten Island, Hyla...   
2    End of Sharrotts Ave at Hylan Blvd, Hylan Blvd...   
3                                                 None   
4                             W 79th St End, Manhattan   
..                                                 ...   
757                      25 9th St, Brooklyn, NY 11215   
758                        Pier 11, Brooklyn, NY 11231   
759              464 Bay Ridge Ave, Brooklyn, NY 11220   
760                                     298 Conover St   
761  South Red Hook, 699 Columbia St, Brooklyn, NY ...   

                                      site_description  \
0    This waterfront park is named, in part, for Ju...   
1    The site of a legendary display of American de...   
2                                                 None   
3                             Yellow trail nature path   
4    This site is considered a cultural resource. R...   
..                                                 ...   
757  The Lowlands Nursery offers plants that are we...   
758  Mary A. Whalen, known as the S.T. Kiddoo from ...   
759  Peaceful volunteer-run 4.5-acre garden featuri...   
760  With several flower blooms as well as a shaded...   
761  The RETI field station is a living, floating l...   

                                       hours_info  \
0       Sunrise to Sunset (April 1 to December 1)   
1       Sunrise to Sunset (April 1 to December 1)   
2                                            None   
3                                            None   
4       Sunrise to Sunset (April 1 to December 1)   
..                                            ...   
757  every Thursday & Saturday from 10 AM to 2 PM   
758              Monday thru Friday 10 am - 6 pm    
759                                  10 am - 5 pm   
760                                  Dawn to dusk   
761                                           NaN   

                                      open_close_date   fee  ...  \
0                                                None  None  ...   
1                                                None     Y  ...   
2                                                None  None  ...   
3                                                None  None  ...   
4                                              

## Create spatial dataframe

 - make map; red points are new or updated

In [120]:
hap_site_points = gpd.GeoDataFrame(new_hap_site_points, geometry=gpd.points_from_xy(new_hap_site_points['x'], new_hap_site_points['y']), crs="EPSG:4326")

In [121]:
m = folium.Map(
    location=[
        hap_site_points['y'].mean(), 
        hap_site_points['x'].mean()
    ], 
    zoom_start=10,
)

#creating a Marker for each point in df_sample. Each point will get a popup with their zip
for row in hap_site_points.itertuples():
        popup_text = f"Site Name: {row.site_name}<br>Activity Codes: {row.act_codes}"
        color = 'blue' if pd.isna(row.Creator) else 'red'
    
        folium.CircleMarker(
            location=[row.y,  row.x],
            radius=4,
            popup=popup_text,
            color=color,  # Change the color of the circle outline
            fill=True,
            fill_color='blue'
        ).add_to(m)
    
m   

### write out the geojson

In [122]:
# hap_site_points.to_file('data/hap_site_points_20230804.geojson', driver='GeoJSON')

### Import acitivity points to update with new survey data

In [318]:
current_act_points = gpd.read_file('data/data_updates/correcting_activity_points_20230814/hap_activity_points_20230815.geojson')

act_points = (
    current_act_points
    .assign(
        lon = raw_act_points['geometry'].apply(lambda geom: geom.x),
        lat = raw_act_points['geometry'].apply(lambda geom: geom.y)
    )
    .drop(columns=['geometry'])
     [['act_id', 'access_id', 'site_id', 'site_name', 'activity', 'access_name', 'lon', 'lat']]
)

act_points

act_id  access_id site_id                         site_name activity  \
0     1453_FISH     1453.0  501734               1st St & W River Rd     FISH   
1     1452_FISH     1452.0  501120               2nd St & William St     FISH   
2     1451_FISH     1451.0  501108               3rd St & William St     FISH   
3      937_FISH      937.0  286080            911 Memorial Weehawken     FISH   
4     1790_FISH     1790.0  181010    Fishing access off Seagirt Ave     FISH   
...         ...        ...     ...                               ...      ...   
1147   211_FISH      211.0  530680              Hans Pedersen & Sons     FISH   
1148    91_FISH       91.0  534902                    Gateway Marina     FISH   
1149  1447_MPBL     1447.0  540232   Fair Haven Rd & Fairwaters Lane     MPBL   
1150   331_HPBL      331.0  595580       Steuben House Historic Site     HPBL   
1151   256_FISH      256.0  639592  Arthur Kill Greenway (Elizabeth)     FISH   

                                            access_name        lon        lat  
0                                                  None -74.014337  40.375910  
1                                                  None -74.015138  40.375671  
2                                                  None -74.016032  40.375349  
3                                                  None -74.010929  40.772841  
4                                                  None -73.741771  40.595561  
...                                                 ...        ...        ...  
1147         Hans Pedersen & Sons, Hans Pederson & Sons -74.255952  40.460953  
1148             Gateway Marina, Schupps Landing Marina -74.208022  40.435564  
1149                    Fair Haven Rd & Fairwaters Lane -73.981869  40.398192  
1150               Historic New Bridge Landing, Main St -74.038462  40.367450  
1151  Arthur Kill Greenway (Elizabeth), Court St & F... -74.030772  40.913625  

[1152 rows x 8 columns]

### Identify sites with no activity point

In [284]:
# site_activity
site_activity_join = (
    hap_site_points[['site_id', 'site_name', 'source']]
    .rename(columns={'site_name': 'site_name_site'})
    .merge(current_act_points, on='site_id', how='outer')
)

# no_acts
no_acts = site_activity_join[site_activity_join['act_id'].isna()]

no_acts
### there are 17

site_id                               site_name_site  \
25    109392                          Brooklyn Yacht Club   
82    147570                           Pilgrim Yacht Club   
83    147662                          Flamingo Yacht Club   
550   540232                              Fair Haven Pier   
1148  900137              American Veterans Memorial Pier   
1149  900138                             Bensonhurst Park   
1150  900139                   Brooklyn Bay Center at BJs   
1151  900140                     Bush Terminal Piers Park   
1152  900141                                Canarsie Park   
1153  900142                     Empire City Water Sports   
1154  900143        Fairway Promenade at Red Hook Stores    
1155  900144                       Greenpoint Public Park   
1156  900145                            Lowlands Nursery    
1157  900146                                MARY A WHALEN   
1158  900147                    Narrows Botanical Gardens   
1159  900148                   Pier 44 Waterfront Garden    
1160  900149  RETI Field Station at Gowanus Bay Terminal    

                          source act_id  access_id site_name activity  \
25                          None    NaN        NaN       NaN      NaN   
82                          None    NaN        NaN       NaN      NaN   
83                          None    NaN        NaN       NaN      NaN   
550           njdep_water_access    NaN        NaN       NaN      NaN   
1148  Alyssa, summer 23 new site    NaN        NaN       NaN      NaN   
1149  Alyssa, summer 23 new site    NaN        NaN       NaN      NaN   
1150  Alyssa, summer 23 new site    NaN        NaN       NaN      NaN   
1151  Alyssa, summer 23 new site    NaN        NaN       NaN      NaN   
1152  Alyssa, summer 23 new site    NaN        NaN       NaN      NaN   
1153  Alyssa, summer 23 new site    NaN        NaN       NaN      NaN   
1154  Alyssa, summer 23 new site    NaN        NaN       NaN      NaN   
1155  Alyssa, summer 23 new site    NaN        NaN       NaN      NaN   
1156  Alyssa, summer 23 new site    NaN        NaN       NaN      NaN   
1157  Alyssa, summer 23 new site    NaN        NaN       NaN      NaN   
1158  Alyssa, summer 23 new site    NaN        NaN       NaN      NaN   
1159  Alyssa, summer 23 new site    NaN        NaN       NaN      NaN   
1160  Alyssa, summer 23 new site    NaN        NaN       NaN      NaN   

     access_name geometry  
25           NaN     None  
82           NaN     None  
83           NaN     None  
550          NaN     None  
1148         NaN     None  
1149         NaN     None  
1150         NaN     None  
1151         NaN     None  
1152         NaN     None  
1153         NaN     None  
1154         NaN     None  
1155         NaN     None  
1156         NaN     None  
1157         NaN     None  
1158         NaN     None  
1159         NaN     None  
1160         NaN     None

In [285]:
## add new survey data
raw_surv_act_new = pd.read_csv('data/data_updates/activity_loc_point_1.csv')

In [286]:
raw_surv_act_new

ObjectID                              GlobalID act_codes  \
0         45  38914c86-724a-40ab-85fe-cbfe7480cb66       NaN   
1         48  e69eef4e-3808-4843-81c3-7ffe4eadbaae      HPBL   
2         49  0d0f0ec4-9469-47af-8555-f878d34e4fc4      FISH   
3         51  572e6db3-43f1-4b29-818a-f9aacd3b149e      HPBL   
4         52  37406c77-eb81-4e23-83b0-789e22af0ab5      HPBL   
5         53  825b9466-f5b0-40aa-87a5-08c08c6d58dc      FISH   
6         54  6eb4c74c-e669-48c4-8ed7-19ecade1446a      FISH   
7         55  cf539a38-c1dd-4546-858b-32967f7189f6      HPBL   
8         56  bc71c10d-7a4b-4f72-8022-d4acf0e22835      MPBL   
9         57  7df25b1f-3d9b-4591-84c1-ea49c3cac535      FISH   
10        58  3f2db069-8300-496b-8e01-7704a9a5a429      FISH   
11        59  93485a7a-edf4-4a3c-8798-aed2e477343c      FISH   
12        60  d6e57859-4a24-4a9c-8290-05bc06e51c1c      FISH   
13        62  e3ea1404-07cf-459a-823f-7bac5f9114d4      FISH   
14        63  79e4cc39-9ece-445a-847a-3826f242ab31      FISH   
15        64  ecab42ef-4c62-47f5-81ee-5f22e004494c      HPBL   
16        65  fb663309-2982-4265-8eaa-0978a86469de      FISH   
17        66  cd1a521a-35b9-44fa-8101-18f335019f03      FISH   
18        67  56c8dfec-5552-4d5d-84bd-9a6e4068a443       NaN   
19        68  39943998-58b3-4807-8288-1b8709c88de7       NaN   
20        69  80cd5df2-9305-4b07-8b04-6e91b821c2e0       NaN   
21        70  ee3da41a-50b0-400d-887e-0c2de3ab4036       NaN   
22        71  f8ef990f-d380-4235-8af6-d503a7b2fbbd       NaN   
23        72  9f845700-21d8-44ee-8593-b4974a18413c       NaN   
24        73  11296a01-35c4-4234-88ad-6878d7c8d1f5       NaN   
25        74  101839be-2f66-4fd1-8bee-21294137a18b       NaN   
26        75  6a5c7db6-32b0-4cdd-8c44-c329470d6773       NaN   
27        76  029c7f13-75bf-4660-8186-fbcdcbe1b16e       NaN   
28        78  362970e8-2a7e-49b0-8ba6-2bb29fc77e1c       NaN   
29        79  0d6f4052-a8b0-4a74-83b9-9fccbeddc2ab       NaN   
30        80  a570832b-69c0-45d4-8d88-4c62b59d6c43       NaN   
31        81  d006ab30-314e-42a9-819b-510170b8b840       NaN   

                               access_name  access_address  \
0   Lowe's Gowanus Parklet and Boat Launch             NaN   
1                                      NaN             NaN   
2                                      NaN             NaN   
3                      Hendrix Creek Pier              NaN   
4                                      NaN             NaN   
5                                Penn Pier             NaN   
6                                      NaN             NaN   
7                                      NaN             NaN   
8                                      NaN             NaN   
9                                      NaN             NaN   
10                                     NaN             NaN   
11                                     NaN             NaN   
12                                     NaN             NaN   
13                                     NaN             NaN   
14                   WNYC Transmitter Pier             NaN   
15                                     NaN             NaN   
16                                     NaN             NaN   
17                                     NaN             NaN   
18              Columbia Street Esplanade              NaN   
19                 Erie Basin Park at IKEA             NaN   
20                       Calvert Vaux Park             NaN   
21                       Calvert Vaux Park             NaN   
22                        Bensonhurst Park             NaN   
23          Pier 44 Waterfront Garden Pier             NaN   
24                       Pier 84 Boathouse             NaN   
25                                 Pier 84             NaN   
26                    Hallett's Cove Beach             NaN   
27                    Hallett's Cove Beach             NaN   
28           Downtown Boathouse at Pier 26             NaN   
29                             

In [327]:
# this is the old sites, can use this to compare later
survey_acts = (
    raw_surv_act_new
    .merge(global_key, left_on='ParentGlobalID', right_on='GlobalID', how='left')
)

survey_acts = (
    survey_acts
    .assign(
        activity = survey_acts.apply(lambda row: row['act_codes'] if pd.isna(row['act_code']) else row['act_code'], axis=1),
        access_name = survey_acts.apply(lambda row: row['site_name'] if pd.isna(row['access_name']) else row['access_name'], axis=1),
        access_id = survey_acts.index + 1800, ### the highest 
    )
    .rename(columns={'x': 'lon', 'y': 'lat'})
     [['access_id', 'site_id', 'site_name', 'activity', 'access_name', 'lon', 'lat']]
)

survey_acts['act_id'] = survey_acts.apply(lambda row: f"{row['access_id']}_{row['activity']}", axis=1)

survey_acts

access_id site_id                             site_name activity  \
0        1800   71975  Lowe's Gowanus Parklet & Boat Launch     HPBL   
1        1801     157               Louis Valentino Jr Park     HPBL   
2        1802     157               Louis Valentino Jr Park     FISH   
3        1803  649119           Shirley Chisholm State Park     HPBL   
4        1804  649119           Shirley Chisholm State Park     HPBL   
5        1805  649119           Shirley Chisholm State Park     FISH   
6        1806      45          Canarsie Pier at Jamaica Bay     FISH   
7        1807      45          Canarsie Pier at Jamaica Bay     HPBL   
8        1808      45          Canarsie Pier at Jamaica Bay     MPBL   
9        1809  900141                         Canarsie Park     FISH   
10       1810     194                  Bay Ridge Kite Field     FISH   
11       1811     161                       Shore Road Park     FISH   
12       1812     161                       Shore Road Park     FISH   
13       1813  900137       American Veterans Memorial Pier     FISH   
14       1814      94                 WNYC Transmitter Park     FISH   
15       1815     134                 East River State Park     HPBL   
16       1816     134                 East River State Park     FISH   
17       1817   79502              North 5th St Pier & Park     FISH   
18       1818     184             Columbia Street Esplanade     FISH   
19       1819     231                       Erie Basin Park     FISH   
20       1820       3                     Calvert Vaux Park     FISH   
21       1821       3                     Calvert Vaux Park     HPBL   
22       1822  900138                      Bensonhurst Park     FISH   
23       1823  900148            Pier 44 Waterfront Garden      FISH   
24       1824  900133            Hudson River Park, Pier 84     HPBL   
25       1825  900133            Hudson River Park, Pier 84     FISH   
26       1826     192                  Hallett's Cove Beach     HPBL   
27       1827     192                  Hallett's Cove Beach     FISH   
28       1828  900124            Hudson River Park, Pier 26     HPBL   
29       1829  900124            Hudson River Park, Pier 26     FISH   
30       1830  645755                    Yonkers Yacht Club     MPBL   
31       1831  645755                    Yonkers Yacht Club     HPBL   

                               access_name        lon        lat     act_id  
0   Lowe's Gowanus Parklet and Boat Launch -73.996945  40.673120  1800_HPBL  
1                  Louis Valentino Jr Park -74.018112  40.678672  1801_HPBL  
2                  Louis Valentino Jr Park -74.019597  40.678400  1802_FISH  
3                      Hendrix Creek Pier  -73.873679  40.645966  1803_HPBL  
4              Shirley Chisholm State Park -73.857275  40.644370  1804_HPBL  
5                                Penn Pier -73.870065  40.638756  1805_FISH  
6             Canarsie Pier at Jamaica Bay -73.883717  40.627819  1806_FISH  
7             Canarsie Pier at Jamaica Bay -73.883962  40.630597  1807_HPBL  
8             Canarsie Pier at Jamaica Bay -73.883890  40.630711  1808_MPBL  
9                            Canarsie Park -73.895239  40.622942  1809_FISH  
10                    Bay Ridge Kite Field -74.024152  40.603996  1810_FISH  
11                         Shore Road Park -74.040989  40.630225  1811_FISH  
12                         Shore Road Park -74.036162  40.609699  1812_FISH  
13         American Veterans Memorial Pier -74.038560  40.639621  1813_FISH  
14                   WNYC Transmitter Pier -73.962489  40.729785  1814_FISH  
15                   East River State Park -73.962599  40.722286  1815_HPBL  
16                   East River State Park -73.963084  40.721870  1816_FISH  
17                North 5th St Pier & Park -73.964100  40.720776  1817_FISH  
18              Columbia Street Esplanade  -74.015172  40.665203  1818_FISH  
19                 Erie Basin Park at IKEA -74.013746  40.669855  1

### Check for existing activity points that are being updated and remove them from current list

In [320]:
# perform a full join of current activity points and the survey activity points and select the activities that are in both
# these will be removed from current and replaced by the surey

updated_activity_points = (
    survey_acts
    .merge(current_act_points, on=['site_id', 'activity'], how='outer', indicator=True)
    .query('_merge == "both"')
    [['site_id', 'activity']]
)

updated_activity_points

site_id activity
0    71975     HPBL
1      157     HPBL
2      157     FISH
3   649119     HPBL
4   649119     HPBL
6       45     FISH
7       45     HPBL
8       45     MPBL
10     194     FISH
11     161     FISH
12     161     FISH
13     161     FISH
14     161     FISH
16      94     FISH
18     134     FISH
19   79502     FISH
20     184     FISH
21     231     FISH
22       3     FISH
26  900133     HPBL
27  900133     HPBL
28  900133     FISH
29     192     HPBL
31  900124     HPBL
32  900124     FISH
33  900124     FISH
34  645755     MPBL

In [329]:
## perform a full join with list of activities to remove, remove merge = both

new_act_points_temp = (
    act_points
    .merge(updated_activity_points, on=['site_id', 'activity'], how='outer', indicator=True)
    .query('_merge == "left_only"')
    .drop(columns=['_merge'])
)
new_act_points_temp

act_id  access_id site_id                         site_name activity  \
0     1453_FISH     1453.0  501734               1st St & W River Rd     FISH   
1     1452_FISH     1452.0  501120               2nd St & William St     FISH   
2     1451_FISH     1451.0  501108               3rd St & William St     FISH   
3      937_FISH      937.0  286080            911 Memorial Weehawken     FISH   
4     1790_FISH     1790.0  181010    Fishing access off Seagirt Ave     FISH   
...         ...        ...     ...                               ...      ...   
1158   211_FISH      211.0  530680              Hans Pedersen & Sons     FISH   
1159    91_FISH       91.0  534902                    Gateway Marina     FISH   
1160  1447_MPBL     1447.0  540232   Fair Haven Rd & Fairwaters Lane     MPBL   
1161   331_HPBL      331.0  595580       Steuben House Historic Site     HPBL   
1162   256_FISH      256.0  639592  Arthur Kill Greenway (Elizabeth)     FISH   

                                            access_name        lon        lat  
0                                                  None -74.014337  40.375910  
1                                                  None -74.015138  40.375671  
2                                                  None -74.016032  40.375349  
3                                                  None -74.010929  40.772841  
4                                                  None -73.741771  40.595561  
...                                                 ...        ...        ...  
1158         Hans Pedersen & Sons, Hans Pederson & Sons -74.255952  40.460953  
1159             Gateway Marina, Schupps Landing Marina -74.208022  40.435564  
1160                    Fair Haven Rd & Fairwaters Lane -73.981869  40.398192  
1161               Historic New Bridge Landing, Main St -74.038462  40.367450  
1162  Arthur Kill Greenway (Elizabeth), Court St & F... -74.030772  40.913625  

[1128 rows x 8 columns]

In [331]:
### add the new points to the old points and make access name site name if it is na

new_act_points = pd.concat([new_act_points_temp, survey_acts], ignore_index=True)

new_act_points['access_name'] = new_act_points.apply(lambda row: row['site_name'] if pd.isna(row['access_name']) else row['access_name'], axis=1)

new_act_points

act_id  access_id site_id                       site_name activity  \
0     1453_FISH     1453.0  501734             1st St & W River Rd     FISH   
1     1452_FISH     1452.0  501120             2nd St & William St     FISH   
2     1451_FISH     1451.0  501108             3rd St & William St     FISH   
3      937_FISH      937.0  286080          911 Memorial Weehawken     FISH   
4     1790_FISH     1790.0  181010  Fishing access off Seagirt Ave     FISH   
...         ...        ...     ...                             ...      ...   
1155  1827_FISH     1827.0     192            Hallett's Cove Beach     FISH   
1156  1828_HPBL     1828.0  900124      Hudson River Park, Pier 26     HPBL   
1157  1829_FISH     1829.0  900124      Hudson River Park, Pier 26     FISH   
1158  1830_MPBL     1830.0  645755              Yonkers Yacht Club     MPBL   
1159  1831_HPBL     1831.0  645755              Yonkers Yacht Club     HPBL   

                         access_name        lon        lat  
0                1st St & W River Rd -74.014337  40.375910  
1                2nd St & William St -74.015138  40.375671  
2                3rd St & William St -74.016032  40.375349  
3             911 Memorial Weehawken -74.010929  40.772841  
4     Fishing access off Seagirt Ave -73.741771  40.595561  
...                              ...        ...        ...  
1155            Hallett's Cove Beach -73.935281  40.769618  
1156   Downtown Boathouse at Pier 26 -74.012820  40.721259  
1157                         Pier 26 -74.015336  40.721399  
1158              Yonkers Yacht Club -73.888117  40.977102  
1159              Yonkers Yacht Club -73.888130  40.977122  

[1160 rows x 8 columns]

## make geospatial activity points

In [336]:
hap_act_points = gpd.GeoDataFrame(new_act_points, geometry=gpd.points_from_xy(new_act_points['lon'], new_act_points['lat']), crs="EPSG:4326")

In [339]:
act_m = folium.Map(
    location=[
        hap_act_points['lat'].mean(), 
        hap_act_points['lon'].mean()
    ], 
    zoom_start=10,
)

#creating a Marker for each point in df_sample. Each point will get a popup with their zip
for row in hap_act_points.itertuples():
        popup_text = f"Site Name: {row.site_name}<br>Activity Codes: {row.activity}"
#         color = 'blue' if pd.isna(row.Creator) else 'red'
    
        folium.CircleMarker(
            location=[row.lat,  row.lon],
            radius=4,
            popup=popup_text,
            color='blue',  # Change the color of the circle outline
            fill=True,
            fill_color='blue'
        ).add_to(act_m)
    
act_m 